In [9]:
import numpy as np
import matplotlib.pyplot as plt
import ffmpeg
import os
from IPython.display import Video
os.makedirs("frames", exist_ok=True) #where to save the images

## 2 Dimensional Visualization of Solution to the Reaction Diffusion Equation

In [10]:
#general code implementation method source: https://pnavaro.github.io/python-fortran/06.gray-scott-model.html
#used chat gpt to help generate some code -- noted and explained
# Parameters determined through: https://jasonwebb.github.io/reaction-diffusion-playground/app.html

## Define Reaction kinetics as defined the in the assignment 
def f(u, v, F):
    return -u*v**2 + F*(1 - u)
def g(u, v, F, k):
    return u*v**2 - (F + k)*v

## Define Laplacian using finite differencing:
def laplacian_2D(x, dx=1):
    #x_i-1,j + x_i,j-1 - 4 x_i,j +x_i+1,j +x_i,j+1 /dx^2
    return (x[:-2, 1:-1] + x[1:-1, :-2] - 4 * x[1:-1, 1:-1] + x[2:, 1:-1] + x[1:-1, 2:]) / dx**2

## Define Spectral Laplacian:source:https://www.youtube.com/watch?v=X7_PcwDcYRU&list=PLISXH-iEM4Jkwdj3JxG-R7zrCV1Ii8axn&index=4
def laplacian_2D_spectral(x, L=1):
    N = x.shape[0]
    kx = 2*np.pi / L * np.fft.fftfreq(N, d=L/N)
    ky = 2*np.pi / L * np.fft.fftfreq(N, d=L/N)
    KX, KY = np.meshgrid(kx, ky, indexing='ij')
    lap_operator = - (KX**2 + KY**2) * np.fft.fft2(x)
    return np.fft.ifft2(lap_operator).real

##Defining periodc Boundary Conditions:
# Periodic BCs: source: https://pnavaro.github.io/python-fortran/06.gray-scott-model.html
def periodic_bc(x):
    x[0,:] = x[-2,:] #right side = left side
    x[-1, :] = x[1,:] # left side = right side
    x[:,0] = x[:,-2] #top = bottom
    x[:,-1] = x[:,1] #bottom = top

##Defining No Flux Boundary Conditions:
def noflux_bc(x): #got chat gpt to explain this conceptually and check that I implemented correctly
    x[0,:] = x[1,:] #right side = right side at 1
    x[-1, :] = x[-2,:]#left side = left side at -2
    x[:,0] = x[:,1] # top = top at neighboring point
    x[:,-1] = x[:,-2] #top = top at neighboring point


def initialize_grid(n): #method and mask values from https://pnavaro.github.io/python-fortran/06.gray-scott-model.html but adapted to create circular initial noise 
    x0, y0 = 0.5, 0.5 #center cirlce
    r = 0.1     
    u = np.ones((n+2, n+2))
    v = np.zeros((n+2, n+2))
    x, y = np.meshgrid(np.linspace(0, 1, n+2), np.linspace(0, 1, n+2))
    mask = (x-x0)**2 + (y- y0)**2 < r**2
    u[mask] = 0.50
    v[mask] = 0.25
    return u, v

## Function containing finite differencing method and appying boundary condition within appropriate grid point domain
def gray_scott_finite_diff(U, V, D_u, D_v, F, k,dt,boundary): #used forward euler and made corrections from https://pnavaro.github.io/python-fortran/06.gray-scott-model.html
    #forward Euler:
    #u_n+t = u_n + dt(D * laplacian + non-linear term)
    U[1:-1, 1:-1] = U[1:-1, 1:-1] + dt*(D_u * laplacian_2D(U) + f(U[1:-1, 1:-1] , V[1:-1, 1:-1], F))
    V[1:-1, 1:-1] = V[1:-1, 1:-1]+ dt*(D_v * laplacian_2D(V) + g(U[1:-1, 1:-1], V[1:-1, 1:-1], F, k))
    #apply the boundary conditions to relevant grid points
    boundary(U)
    boundary(V)
    return U, V

#Set 1 of parametesr
Du, Dv = 0.2043, 0.0360 
F, k = 0.0474, 0.0696
n = 200  # grid size 
NT = 500  #time steps
dt = 1

U, V = initialize_grid(n)

plt.ioff()
for i in range(NT):
    fig = plt.figure(figsize = (5,5))
    #source/structure from  https://pnavaro.github.io/python-fortran/06.gray-scott-model.html
     #for each time step you can add a for loop to create an image for 10 extra time 
     #steps which allows for more efficiency since you are creating an image for each
     #10th step- method from  https://pnavaro.github.io/python-fortran/06.gray-scott-model.html 
    for time in range(10):
        U, V = gray_scott_finite_diff(U, V, Du, Dv, F, k,dt,periodic_bc)
    
    V_plot = (V[1:-1, 1:-1] - V[1:-1, 1:-1].min()) / (V[1:-1, 1:-1].ptp()) #normalization - chat gpt helped correct my code here using ptp which essentially gets V.max-V.min
    plt.imshow(V_plot, cmap='viridis')
    plt.colorbar(label='[V]')
    plt.title(f'Reaction-Diffusion (Gray-Scott)')
    plt.savefig(f"frames/frame_{i:04d}.png")
    plt.close()

!ffmpeg -y -framerate 10 -i frames/frame_%04d.png -c:v libx264 -pix_fmt yuv420p grayscott.mp4



ffmpeg version 7.1.1 Copyright (c) 2000-2025 the FFmpeg developers
  built with Apple clang version 16.0.0 (clang-1600.0.26.6)
  configuration: --prefix=/opt/homebrew/Cellar/ffmpeg/7.1.1_1 --enable-shared --enable-pthreads --enable-version3 --cc=clang --host-cflags= --host-ldflags='-Wl,-ld_classic' --enable-ffplay --enable-gnutls --enable-gpl --enable-libaom --enable-libaribb24 --enable-libbluray --enable-libdav1d --enable-libharfbuzz --enable-libjxl --enable-libmp3lame --enable-libopus --enable-librav1e --enable-librist --enable-librubberband --enable-libsnappy --enable-libsrt --enable-libssh --enable-libsvtav1 --enable-libtesseract --enable-libtheora --enable-libvidstab --enable-libvmaf --enable-libvorbis --enable-libvpx --enable-libwebp --enable-libx264 --enable-libx265 --enable-libxml2 --enable-libxvid --enable-lzma --enable-libfontconfig --enable-libfreetype --enable-frei0r --enable-libass --enable-libopencore-amrnb --enable-libopencore-amrwb --enable-libopenjpeg --enable-libspeex

In [12]:
Video("grayscott.mp4", embed=True)

In [4]:
## for different parameters:
## same code so I didnt comment all of the steps again: 
os.makedirs("frames2", exist_ok=True) 

Du, Dv = 0.2043, 0.0360
F, k = 0.0540, 0.0616
n = 200 
NT = 500
dt = 1

U, V = initialize_grid(n)
plt.ioff()
for i in range(NT):
    fig = plt.figure(figsize = (5,5))
    for time in range(10):
        U, V = gray_scott_finite_diff(U, V, Du, Dv, F, k,dt,periodic_bc)
    V_plot = (V[1:-1, 1:-1] - V[1:-1, 1:-1].min()) / (V[1:-1, 1:-1].ptp()) 
    plt.imshow(V_plot, cmap='viridis')
    plt.colorbar(label='[V]')
    plt.title(f'Reaction-Diffusion (Gray-Scott)')
    plt.savefig(f"frames2/frame_{i:04d}.png")
    plt.close()

!ffmpeg -y -framerate 10 -i frames2/frame_%04d.png -c:v libx264 -pix_fmt yuv420p grayscott2.mp4

ffmpeg version 7.1.1 Copyright (c) 2000-2025 the FFmpeg developers
  built with Apple clang version 16.0.0 (clang-1600.0.26.6)
  configuration: --prefix=/opt/homebrew/Cellar/ffmpeg/7.1.1_1 --enable-shared --enable-pthreads --enable-version3 --cc=clang --host-cflags= --host-ldflags='-Wl,-ld_classic' --enable-ffplay --enable-gnutls --enable-gpl --enable-libaom --enable-libaribb24 --enable-libbluray --enable-libdav1d --enable-libharfbuzz --enable-libjxl --enable-libmp3lame --enable-libopus --enable-librav1e --enable-librist --enable-librubberband --enable-libsnappy --enable-libsrt --enable-libssh --enable-libsvtav1 --enable-libtesseract --enable-libtheora --enable-libvidstab --enable-libvmaf --enable-libvorbis --enable-libvpx --enable-libwebp --enable-libx264 --enable-libx265 --enable-libxml2 --enable-libxvid --enable-lzma --enable-libfontconfig --enable-libfreetype --enable-frei0r --enable-libass --enable-libopencore-amrnb --enable-libopencore-amrwb --enable-libopenjpeg --enable-libspeex

In [6]:
Video("grayscott2.mp4", embed=True)

In [7]:
## for different parameters:
## same code so I didnt comment all of the steps again: 
plt.ioff()
os.makedirs("frames3", exist_ok=True)

Du, Dv = 0.2097, 0.1050
F, k = 0.0082, 0.0451
n = 200 
NT = 5000 
dt = 1

U, V = initialize_grid(n)
plt.ioff()
for i in range(NT):
    fig3 = plt.figure(figsize = (5,5))
    for time in range(3):
        U, V = gray_scott_finite_diff(U, V, Du, Dv, F, k,dt,noflux_bc)
    V_plot = (V[1:-1, 1:-1] - V[1:-1, 1:-1].min()) / (V[1:-1, 1:-1].ptp())
    plt.imshow(V_plot, cmap='plasma')
    plt.colorbar(label='[V]')
    plt.title(f'Reaction-Diffusion (Gray-Scott)')
    plt.savefig(f"frames3/frame_{i:04d}.png")
    plt.close()

!ffmpeg -y -framerate 200 -i frames3/frame_%04d.png -c:v libx264 -pix_fmt yuv420p grayscott3.mp4

ffmpeg version 7.1.1 Copyright (c) 2000-2025 the FFmpeg developers
  built with Apple clang version 16.0.0 (clang-1600.0.26.6)
  configuration: --prefix=/opt/homebrew/Cellar/ffmpeg/7.1.1_1 --enable-shared --enable-pthreads --enable-version3 --cc=clang --host-cflags= --host-ldflags='-Wl,-ld_classic' --enable-ffplay --enable-gnutls --enable-gpl --enable-libaom --enable-libaribb24 --enable-libbluray --enable-libdav1d --enable-libharfbuzz --enable-libjxl --enable-libmp3lame --enable-libopus --enable-librav1e --enable-librist --enable-librubberband --enable-libsnappy --enable-libsrt --enable-libssh --enable-libsvtav1 --enable-libtesseract --enable-libtheora --enable-libvidstab --enable-libvmaf --enable-libvorbis --enable-libvpx --enable-libwebp --enable-libx264 --enable-libx265 --enable-libxml2 --enable-libxvid --enable-lzma --enable-libfontconfig --enable-libfreetype --enable-frei0r --enable-libass --enable-libopencore-amrnb --enable-libopencore-amrwb --enable-libopenjpeg --enable-libspeex

In [8]:
Video("grayscott3.mp4", embed=True)